In [5]:
import nbaScraper as ns
import actNetScraper as ans
from datetime import datetime, timedelta

database_export = True
store_locally = True

# nba website, basketball referenece scraper
scraper = ns.scraper(
    browser_path = '..\\..\\browser\\geckodriver.exe',
    database_export = database_export, 
    store_locally = store_locally,
    pymysql_conn_str =  None
)
today = scraper.meta_data['today_dt']
lastNgames = 10
day_adj = -1

### prop line/odd scraper
leagues =  None # None or list ['nba', 'nhl', 'nfl']
specified =  []
# day adjustment from today (date of running script), negative = dates into the past
dayJump = 0 
# date can be a list of dates if multiple need scraping 'YYYY-MM-DD'
# default is to only pull today or today + dayJump
dates = [(datetime.today() + timedelta(days=dayJump)).strftime('%Y-%m-%d')]
#dates = ['2024-01-05', '2024-01-06', '2024-01-07', '2024-01-08', '2024-01-09', '2024-01-10', '2024-01-11']

prop_scraper = ans.actNetScraper(
    browser_path = '..\\..\\browser\\geckodriver.exe',
    dates = dates,
    leagues = leagues,
    database_export = database_export, 
    store_locally = store_locally,
    config_path = '..\\..\\..\\..\\Notes-General\\config.txt',
    second_run = False
)

# turn to False if issues loading new players
#prop_scraper.update_players = False

# update the league list to only ones with games today
#leagues = prop_scraper.check_for_league_games(date_check = None, update_class_leagues_var = True)
print('scraping for', prop_scraper.leagues, 'on', prop_scraper.run_date_str)

scraping for ['nfl', 'nba', 'nhl'] on 2025-01-13


In [6]:
prop_scraper.scrape(
    sleep_secs = 3, 
    specific_props = specified,
    leagues_override = leagues,
    an_state_code = 'BC'
)


In [8]:
prop_scraper.processScrapes(
    remove_dups = True,
    specific_props = specified
)

if prop_scraper.scrape_error_flag:
    print(prop_scraper.scrape_errors)
    #prop_scraper.tryMissingProps()


scraping nfl ...
[111816, 137, 249239, '2025-01-13', 'tdOne', None, 674, nan, nan, 0.12919896640826872, -0.009198966408268734, 5, 'D+', nan, nan, nan, nan, 66581715]
[195058, 137, 249239, '2025-01-13', 'tdOne', None, 467, nan, nan, 0.1763668430335097, -0.0563668430335097, 4, 'F', nan, nan, nan, nan, 66581715]
[62984, 137, 249239, '2025-01-13', 'tdOne', None, -130, nan, nan, 0.5652173913043478, -0.05521739130434783, 4, 'F', nan, nan, nan, nan, 66581715]
[196105, 1325, 249239, '2025-01-13', 'tdOne', None, 1536, nan, nan, 0.061124694376528114, -0.03112469437652812, 4, 'D', nan, nan, nan, nan, 66581715]
[195440, 1325, 249239, '2025-01-13', 'tdOne', None, 1092, nan, nan, 0.08389261744966443, 0.00610738255033557, 5, 'C-', nan, nan, nan, nan, 66581715]
[87636, 1325, 249239, '2025-01-13', 'tdOne', None, 382, nan, nan, 0.2074688796680498, 0.02253112033195021, 5, 'C-', nan, nan, nan, nan, 66581715]
[84238, 1325, 249239, '2025-01-13', 'tdOne', None, 395, nan, nan, 0.20202020202020202, -0.10202020

In [4]:
prop_scraper.data_all['nba']

Empty DataFrame
Columns: [propId, playerId, teamId, gameId, date, prop, line, oOdds, uOdds, projValue, oImpValue, oEdge, oQual, oGrade, uImpValue, uEdge, uQual, uGrade]
Index: []

In [ ]:
scraper.get_nba_team_playtype_data(
    base_url = 'https://www.nba.com/stats/teams/{playtype}?TypeGrouping={sideofball}&SeasonType={type}',
    play_types = [
        'isolation', 'transition', 'ball-handler', 'roll-man', 'playtype-post-up',
        'spot-up', 'hand-off', 'cut', 'off-screen','putbacks'
    ],
    sides = ['offensive', 'defensive'],
    season_type = 'Regular+Season',  # ['Regular+Season', 'PlayIn', 'Playoffs']
    database_table = 'statsteamplaytypes'
)


scraper.get_nba_team_shotzone_data(
    base_url = 'https://www.nba.com/stats/teams/{sideOfBall}?DistanceRange=By+Zone&LastNGames={lastNgames}&SeasonType={type}&DateTo={endDate}', 
    sides = {'offensive':'shooting', 'defensive':'opponent-shooting'},
    season_type = 'Regular+Season',  # ['Regular+Season', 'PlayIn', 'Playoffs']
    lastNgames = lastNgames,
    database_table = 'statsteamshotzones',
    endDate = today
)

scraper.get_nba_player_playtype_data(
    base_url = 'https://www.nba.com/stats/players/{playtype}?TypeGrouping={sideofball}&SeasonType={type}', 
    play_types = [
        'isolation', 'transition', 'ball-handler', 'roll-man', 'playtype-post-up',
        'spot-up', 'hand-off', 'cut', 'off-screen','putbacks'
    ],
    sides = ['offensive'],
    season_type = 'Regular+Season',  # ['Regular+Season', 'PlayIn', 'Playoffs']
    database_table = 'statsplayerplaytypes'
)

scraper.get_nba_player_shotzone_data(
    base_url = 'https://www.nba.com/stats/players/shooting?DistanceRange=By+Zone&LastNGames={lastNgames}&SeasonType={type}&DateTo={endDate}', 
    season_type = 'Regular+Season',  # ['Regular+Season', 'PlayIn', 'Playoffs']
    lastNgames = lastNgames,
    database_table = 'statsplayershotzones',
    endDate = today
)

scraper.get_nba_player_passing_data(
    base_url = 'https://www.nba.com/stats/players/passing?DateFrom={d1}&DateTo={d2}&LastNGames=0&PerMode=Totals&SeasonType={type}', 
    today_date = today,
    day_adjuster = day_adj,
    season_type = 'Regular+Season',  # ['Regular+Season', 'PlayIn', 'Playoffs']
    #lastNgames = 10,
    database_table = 'statsplayerpassing'
)

scraper.get_nba_player_rebounding_data(
    base_url = 'https://www.nba.com/stats/players/rebounding?DateFrom={d1}&DateTo={d2}&LastNGames=0&PerMode=Totals&SeasonType={type}', 
    today_date = today,
    day_adjuster = day_adj,
    season_type = 'Regular+Season',  # ['Regular+Season', 'PlayIn', 'Playoffs']
    #lastNgames = 10,
    database_table = 'statsplayerrebounding'
)

scraper.get_bref_pos_estimates(
        base_url = 'https://www.basketball-reference.com/teams/{team}/{season}.html#pbp', 
        today_date = today,
        season = 2025,
        database_table = 'brefmisc'
)

if scraper.scrape_error_flag:
    print(scraper.scrape_errors)

In [ ]:
#prop_scraper.tryMissingProps()
# this didn't work as expected, 
#### added SOG to the nba scrape_errors
#### added new key-value pair for the missing prop:  'missing_dates': ['sog', '2025-01-02', 0]

In [11]:
prop_scraper.scrape_errors

{'nfl': {'missing_dates': [], 'missing_props': [], 'db': []}}

In [7]:
missing = prop_scraper.scrape_errors
del missing['nfl']
#prop_scraper.scrape_errors

In [ ]:
# scrape missed props
import random
wait_secs = random.randint(1,5)

for k, v in missing.items():

    if len(v['missing_props']) > 0:
        leagues_with_missing_props = [k]
        missing_props = v['missing_props']
        print('rescraping', k, 'for', missing_props)

        prop_scraper_missing = ans.actNetScraper(
            browser_path = '..\\..\\browser\\geckodriver.exe',
            dates = dates,
            leagues = leagues_with_missing_props,
            database_export = database_export, 
            store_locally = store_locally,
            config_path = '..\\..\\..\\..\\Notes-General\\config.txt',
            second_run=True
        )

        prop_scraper_missing.scrape(
            sleep_secs = wait_secs, 
            specific_props = missing_props,
            leagues_override = None
        )

        prop_scraper_missing.processScrapes(
            remove_dups = True,
            specific_props = missing_props
        )

In [4]:
import json, time, requests, random
import pandas as pd
import numpy as np
from datetime import datetime, timedelta

from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.wait import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
from selenium.common.exceptions import NoSuchElementException
from bs4 import BeautifulSoup
from sqlalchemy import create_engine

In [12]:
from bs4 import BeautifulSoup

In [ ]:

columns = [
                'propId','playerId','teamId', 'gameId', 'date', 
                'prop', 'line', 'oOdds', 'uOdds', 'projValue', 
                'oImpValue', 'oEdge', 'oQual', 'oGrade',
                'uImpValue', 'uEdge', 'uQual', 'uGrade', 'actNetPropId'
            ]
            # df to hold all data from each loop below. 
            # doesn't need actNetPropId column, it is only used for the loop to combine over and unders
df_props = pd.DataFrame(columns=columns[:-1])

all_props_single_type = {}

In [20]:
for i in prop_scraper.map_option_ids['nba'].keys():
    print(i)

core_bet_type_27_points
core_bet_type_23_rebounds
core_bet_type_26_assists
core_bet_type_21_3fgm
core_bet_type_24_steals
core_bet_type_25_blocks
core_bet_type_85_points_rebounds_assists
core_bet_type_86_points_rebounds
core_bet_type_87_points_assists
core_bet_type_88_rebounds_assists
core_bet_type_89_steals_blocks


In [23]:
base = 'https://api.actionnetwork.com/web/v1/leagues/4/props/{}?bookIds=15,369&date=20250113'
prop = 'pts'
league = 'nba'

In [6]:
service = Service('..\\..\\browser\\geckodriver.exe')
driver = webdriver.Firefox(service=service)
driver.set_page_load_timeout(5)


In [16]:
#driver.get('https://api.actionnetwork.com/web/v1/leagues/4/props/core_bet_type_27_points?date=20250113')
#response = driver.page_source
response = prop_scraper.map_option_ids['nba']['core_bet_type_27_points']['html_str_responses'][0]
response

'<html platform="win" class="theme-dark" dir="ltr"><head><meta http-equiv="Content-Security-Policy" content="default-src \'none\'; script-src resource:; img-src \'self\';"><link rel="stylesheet" type="text/css" href="chrome://devtools-jsonview-styles/content/main.css"><script type="text/javascript" charset="utf-8" async="" data-requirecontext="_" data-requiremodule="viewer-config" src="resource://devtools/client/jsonview/viewer-config.js"></script><script type="text/javascript" charset="utf-8" async="" data-requirecontext="_" data-requiremodule="json-viewer" src="resource://devtools/client/jsonview/json-viewer.js"></script><script type="text/javascript" charset="utf-8" async="" data-requirecontext="_" data-requiremodule="devtools/client/shared/vendor/react-dom" src="resource://devtools/client/shared/vendor/react-dom.js"></script><script type="text/javascript" charset="utf-8" async="" data-requirecontext="_" data-requiremodule="devtools/client/shared/react-utils" src="resource://devtool

In [15]:
parsed_html = BeautifulSoup(response, 'html.parser')
parsed_html

<html class="theme-dark" dir="ltr" platform="win"><head><meta content="default-src 'none'; script-src resource:; img-src 'self';" http-equiv="Content-Security-Policy"/><link href="chrome://devtools-jsonview-styles/content/main.css" rel="stylesheet" type="text/css"/><script async="" charset="utf-8" data-requirecontext="_" data-requiremodule="viewer-config" src="resource://devtools/client/jsonview/viewer-config.js" type="text/javascript"></script><script async="" charset="utf-8" data-requirecontext="_" data-requiremodule="json-viewer" src="resource://devtools/client/jsonview/json-viewer.js" type="text/javascript"></script><script async="" charset="utf-8" data-requirecontext="_" data-requiremodule="devtools/client/shared/vendor/react-dom" src="resource://devtools/client/shared/vendor/react-dom.js" type="text/javascript"></script><script async="" charset="utf-8" data-requirecontext="_" data-requiremodule="devtools/client/shared/react-utils" src="resource://devtools/client/shared/react-util

In [ ]:


html_target_element = parsed_html.find("div", {"id": "json"}).text
json_single_date = json.loads(html_target_element)

books = json_single_date['markets'][0]['books']
len(books)

In [17]:

books = json_single_date['markets'][0]['books']
book_count = len(books)

# if multiple books, use 15, which is the consensus odds
# else, default to the first book in the data
book = 0
if book_count > 1:
    for b in range(0,len(books)):
        print(b)
        if books[b]['book_id'] == 15:
            book = b
            
        else:    
            continue

books[book]['book_id']

15

In [26]:
# looping through all of the props for a single type and single day
for j in json_single_date['markets'][0]['books'][book]['odds']:

        #props_single_date = []
        entry = [np.nan] * (len(columns) - 1)

        # check for odds for the prop on the date
        #IT LOOKS LIKE THEY REMOVED statusCode sometime between 1/6/25 and 1/13/25
        ##if j.get("statusCode") is not None:
        ##    continue
        ##else:
        playerId = j['player_id']

        # actnet propId are not unique in MLB or NHL, creating own propId later
        actNetPropId = j['prop_id']

        ## creating custom propId
        # random number doesn't work because the random num changes when having to combine over and under
        #propId = int(str(j['prop_id']) + str(random.random())[2:6])
        propId = int(str(j['prop_id']) + str(playerId))
                    
        ou_check = j['option_type_id']

        # if the player is not in this dict, it will be added. if it is in then
        # only the odds that are not present will be added
        if all_props_single_type.get(propId) is None:
            
            entry[0] = playerId
            entry[1] = j['team_id']
            entry[2] = j['game_id']
            entry[3] = '2025-01-13'
            entry[4] = prop
            entry[5] = j['value']  # line
            entry[17] = actNetPropId # actnetpropId
            
            #the null value from json comes through strange into pandas, forcing nan
            if pd.isnull(j['projected_value']):
                entry[8] = np.nan
            else:
                entry[8] = j['projected_value']
                            
            #overs and props that don't have over/under designated
            if ou_check in prop_scraper.over_ids[league] or ou_check not in prop_scraper.under_ids[league]:
                entry[6] = j['money'] # over odds
            
                #the null value from json comes through strange into pandas, forcing nan
                if pd.isnull(j['bet_quality'])   :
                    entry[11] = np.nan
                else:
                    entry[11] = j['bet_quality']
                    
                # data point only available in the more recent games
                if j.get('implied_value') is not None:
                    entry[9] = j['implied_value']
                    entry[10] = j['edge']
                    entry[12] = j['grade']
                    
            #unders
            else:
                entry[7] = j['money'] # under odds
            
                #the null value from json comes through strange into pandas, forcing nan
                if pd.isnull(j['bet_quality'])   :
                    entry[15] = np.nan
                else:
                    entry[15] = j['bet_quality']

                # data point only available in the more recent games
                if j.get('implied_value') is not None:
                    entry[13] = j['implied_value']
                    entry[14] = j['edge']
                    entry[16] = j['grade']

            # loading over and under data to the prop id
            all_props_single_type[propId] = entry
        
        # adding the over or under to the existing propId key
        else:
            #overs
            if ou_check in prop_scraper.over_ids[league] or ou_check not in prop_scraper.under_ids[league]:
                all_props_single_type[propId][6] = j['money'] # over odds
            
                #the null value from json comes through strange into pandas, forcing nan
                if pd.isnull(j['bet_quality'])   :
                    all_props_single_type[propId][11] = np.nan
                else:
                    all_props_single_type[propId][11] = j['bet_quality']
                    
                # data point only available in the more recent games
                if j.get('implied_value') is not None:
                    all_props_single_type[propId][9] = j['implied_value']
                    all_props_single_type[propId][10] = j['edge']
                    all_props_single_type[propId][12] = j['grade']
                    

            #unders
            else:
                all_props_single_type[propId][7] = j['money'] # under odds
            
                #the null value from json comes through strange into pandas, forcing nan
                if pd.isnull(j['bet_quality'])   :
                    all_props_single_type[propId][15] = np.nan
                else:
                    all_props_single_type[propId][15] = j['bet_quality']

                # data point only available in the more recent games
                if j.get('implied_value') is not None:
                    all_props_single_type[propId][13] = j['implied_value']
                    all_props_single_type[propId][14] = j['edge']
                    all_props_single_type[propId][16] = j['grade']              
        try:
            # gather player names
            players = json_single_date['markets'][0]['players']
            for p in players:
                player = [p['id'], p['full_name'], p['abbr']]
                prop_scraper.player_list.append(player)
            prop_scraper.players_avail = True
        except: 
            continue

# store the data from this loop                
temp = pd.DataFrame(all_props_single_type.values(), 
index=all_props_single_type.keys(), 
columns=columns[1:]
).reset_index(names=['propId'])

# overwrite the composite propId with the actnetId
temp.loc[:,'propId'] = temp['actNetPropId']
del temp['actNetPropId']

# combine the data from the single loop with all the data    
df_props = pd.concat([df_props, temp])

if True:#self.players_avail:
    # aggregating player to single df 
    df_players = pd.DataFrame(prop_scraper.player_list, columns=prop_scraper.columns_players)           
    df_players.drop_duplicates('playerId', inplace=True)
    
    # merge player names to odds
    df_props = df_props.merge(df_players, on= 'playerId')


# when pulling data after the league games start for the day then live bets might be present
# this should remove them
if True:
    #remove duplicates before loading to database - and print number of drops
    print("original rows: ", df_props.shape)
    df_props = df_props.sort_values(
        ['playerId', 'prop', 'projValue'], 
        ascending=False
    )
    df_props.drop_duplicates(
        subset=['playerId', 'prop'], 
        inplace=True
    )
    # keeps first occurance which should be original after sorting.
    print("after dups removed: ", df_props.shape)

original rows:  (100, 20)
after dups removed:  (100, 20)


In [27]:
df_players

playerId              player          abbr
0         27       Nicolas Batum       N.Batum
1         33        Tim Hardaway    T.Hardaway
2         42     Dennis Schroder    D.Schroder
3        107        Kelly Olynyk      K.Olynyk
4        112        Terry Rozier      T.Rozier
..       ...                 ...           ...
95    281392  Carlton Carrington  C.Carrington
96    281395       Dalton Knecht      D.Knecht
97    281401      Kyshawn George      K.George
98    281423        Jaylen Wells       J.Wells
99    281429         Jamal Shead       J.Shead

[100 rows x 3 columns]